# [Research Task - Create visuals for PUC 99314.11 leg report](https://github.com/cal-itp/data-analyses/issues/1656)
1. line graph of each metric (UPT, VRM, PMT) by agency
- x-axis is year
- y-axis is metric
- each line is an agency
- dotted line is average metric for all agencies in the year

2. line graph of each metric, by district
- similar to above
- each line is a district
- dotted line is average metrics for all districts the year

3. line graph of each metric, by mode
- similar to above
- each line is a mode
- dotter line is average metric for all modes in the year

Maybe try a box plot to show min/max/average for each metric?

## NTD Policy Manual for collecting UPT and PMT

### NTD Full Reporting Policy Manual 
However, FTA recognizes that certain statistics are challenging to collect and can drastically increase the reporting burden for transit agencies. To assist reporters who would find conducting 100 percent count burdensome, `transit agencies may estimate Unlinked Passenger Trips (UPT) and PMT through sampling`. The NTD provides a sampling method and sampling guidance on the NTD website.

### NTD Full Reporting Policy Manual & NTD Reduced Reporting Polict Manual
Collecting Service Consumed Data Transit agencies must report actual data on the Annual Report for all service data except UPT and PMT. `Only Full Reporters report PMT data to the NTD.` For these two data points, agencies may provide an estimate but only if the actual 100 percent data are not reliably collected and routinely processed.



In [2]:
import altair as alt
import pandas as pd
from calitp_data_analysis.sql import get_engine, to_snakecase, query_sql

pd.set_option("display.max_rows", None)
pd.set_option("display.max_columns", None)
pd.set_option("display.max_colwidth", None)

## Data querying, comparing, cleaning

### warehouse query

In [3]:
metric_list = [
    "pmt",
    "upt",
    "vrh",
    # "opexp_total" # not needed for this project
]

# empty list for appending DFs
df_list = []

for metric in metric_list:
        query = f"""
        SELECT
          ntd_id,
          source_agency,
          agency_status,
          primary_uza_name,
          uza_population,
          uza_area_sq_miles,
          year,
          mode,
          type_of_service,
          reporter_type,
          SUM({metric}) AS total_{metric},
        FROM
          `cal-itp-data-infra.mart_ntd_funding_and_expenses.fct_service_data_and_operating_expenses_time_series_by_mode_{metric}`
        WHERE
          source_state = "CA"
          AND year BETWEEN 2018 AND 2023
        GROUP BY
          ntd_id,
          source_agency,
          agency_status,
          primary_uza_name,
          uza_population,
          uza_area_sq_miles,
          year,
          mode,
          type_of_service,
          reporter_type
        """
        # create df
        metric = query_sql(query, as_df=True)

        # append df to list
        df_list.append(metric)

# unpack list into separate DFs
ntd_pmt, ntd_upt, ntd_vrh = df_list

In [5]:
# get districts for ntd ID


for metric in metric_list:
        query = f"""
        SELECT
          `mart_transit_database.dim_organizations`.`key` AS `key`,
          `mart_transit_database.dim_organizations`.`source_record_id` AS `source_record_id`,
          `mart_transit_database.dim_organizations`.`name` AS `name`,
          `mart_transit_database.dim_organizations`.`ntd_id_2022` AS `ntd_id_2022`,
          `Bridge_Organizations_X_Headquarters_County_Geography___Key`.`county_geography_name` AS `county`,
          `Dim_County_Geography___County_Geography_Key`.`caltrans_district` AS `caltrans_district`
        FROM
          `mart_transit_database.dim_organizations`

        LEFT JOIN `mart_transit_database.bridge_organizations_x_headquarters_county_geography` AS `Bridge_Organizations_X_Headquarters_County_Geography___Key` ON `mart_transit_database.dim_organizations`.`key` = `Bridge_Organizations_X_Headquarters_County_Geography___Key`.`organization_key`
          LEFT JOIN `mart_transit_database.dim_county_geography` AS `Dim_County_Geography___County_Geography_Key` ON `Bridge_Organizations_X_Headquarters_County_Geography___Key`.`county_geography_key` = `Dim_County_Geography___County_Geography_Key`.`key`
        WHERE
          (
            `mart_transit_database.dim_organizations`.`_is_current` = TRUE
          )

           AND (
            `mart_transit_database.dim_organizations`.`ntd_id_2022` IS NOT NULL
          )
          AND (
            (
              `mart_transit_database.dim_organizations`.`ntd_id_2022` <> ''
            )

            OR (
              `mart_transit_database.dim_organizations`.`ntd_id_2022` IS NULL
            )
          )
          AND (
            `Bridge_Organizations_X_Headquarters_County_Geography___Key`.`_is_current` = TRUE
          )
          AND (
            `Dim_County_Geography___County_Geography_Key`.`_is_current` = TRUE
          )
        """
        # create df
        ntd_id_x_district = query_sql(query, as_df=True)
        
ntd_id_x_district["caltrans_district"] = ntd_id_x_district["caltrans_district"].astype("str")

In [6]:
ntd_id_x_district.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 246 entries, 0 to 245
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   key                246 non-null    object
 1   source_record_id   246 non-null    object
 2   name               246 non-null    object
 3   ntd_id_2022        246 non-null    object
 4   county             246 non-null    object
 5   caltrans_district  246 non-null    object
dtypes: object(6)
memory usage: 11.7+ KB


In [7]:
merge_on_col = [
    "ntd_id",
    "year",
    "source_agency",
    "agency_status",
    "primary_uza_name",
    "uza_population",
    "uza_area_sq_miles",
    "mode",
    "type_of_service",
    "reporter_type",
]

merge_1 = ntd_vrh.merge(ntd_upt, on=merge_on_col, how="inner")
# merge_2 = merge_1.merge(ntd_vrh, on=merge_on_col, how = "inner")

ntd_metrics_merge = merge_1.merge(ntd_pmt, on=merge_on_col, how="inner")

In [8]:
ntd_metrics_merge.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3342 entries, 0 to 3341
Data columns (total 13 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   ntd_id             3342 non-null   object 
 1   source_agency      3342 non-null   object 
 2   agency_status      3342 non-null   object 
 3   primary_uza_name   2640 non-null   object 
 4   uza_population     3342 non-null   int64  
 5   uza_area_sq_miles  3342 non-null   float64
 6   year               3342 non-null   int64  
 7   mode               3342 non-null   object 
 8   type_of_service    3342 non-null   object 
 9   reporter_type      3342 non-null   object 
 10  total_vrh          2585 non-null   float64
 11  total_upt          2585 non-null   float64
 12  total_pmt          1274 non-null   float64
dtypes: float64(4), int64(2), object(7)
memory usage: 365.5+ KB


### data from other report

In [9]:
# gcs_path = "gs://calitp-analytics-data/data-analyses/ntd/"
# ntd_name = "ntd_operator_data_18_23.parquet"

# ntd_all_metrics = pd.read_parquet(f"{gcs_path}{ntd_name}")

### compare datasets

In [10]:
# display(
#     ntd_all_metrics.info(), ntd_metrics_merge.info()  # mode/service is aggregated up
# )

In [11]:
# display(
#     ntd_all_metrics["ntd_id"].nunique()
#     == ntd_metrics_merge["ntd_id"].nunique(),  # TRUE, same count of unique values
#     set(ntd_all_metrics["ntd_id"].unique())
#     == set(ntd_metrics_merge["ntd_id"].unique()),  # TRUE, same unique NTD_IDs
# )

In [12]:
# display(
#     ntd_all_metrics["ntd_id"].nunique(),
#     ntd_metrics_merge["ntd_id"].nunique()
# )

In [13]:
# metric_cols = ["total_upt", "total_vrh", "total_upt"]

# for metric in metric_cols:
#     print(
#         ntd_all_metrics[metric].sum() == ntd_metrics_merge[metric].sum()
#     )  # TRUE sum of each metrics are equal

### merge in the district numbers to ntd_metric_merge

In [14]:
ntd_metrics_merge = ntd_metrics_merge.merge(
    ntd_id_x_district[["ntd_id_2022","county","caltrans_district"]],
    left_on = "ntd_id",
    right_on = "ntd_id_2022",
    how="inner",
    indicator=True
)

In [15]:
ntd_metrics_merge.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3252 entries, 0 to 3251
Data columns (total 17 columns):
 #   Column             Non-Null Count  Dtype   
---  ------             --------------  -----   
 0   ntd_id             3252 non-null   object  
 1   source_agency      3252 non-null   object  
 2   agency_status      3252 non-null   object  
 3   primary_uza_name   2556 non-null   object  
 4   uza_population     3252 non-null   int64   
 5   uza_area_sq_miles  3252 non-null   float64 
 6   year               3252 non-null   int64   
 7   mode               3252 non-null   object  
 8   type_of_service    3252 non-null   object  
 9   reporter_type      3252 non-null   object  
 10  total_vrh          2525 non-null   float64 
 11  total_upt          2525 non-null   float64 
 12  total_pmt          1274 non-null   float64 
 13  ntd_id_2022        3252 non-null   object  
 14  county             3252 non-null   object  
 15  caltrans_district  3252 non-null   object  
 16  _merge

In [16]:
ntd_metrics_merge[ntd_metrics_merge["_merge"]=="left_only"]["source_agency"].value_counts().head()

Series([], Name: source_agency, dtype: int64)

In [17]:
ntd_metrics_merge[ntd_metrics_merge["caltrans_district"].isna()].head()

Empty DataFrame
Columns: [ntd_id, source_agency, agency_status, primary_uza_name, uza_population, uza_area_sq_miles, year, mode, type_of_service, reporter_type, total_vrh, total_upt, total_pmt, ntd_id_2022, county, caltrans_district, _merge]
Index: []

## save out data

In [4]:
gcs_path = "gs://calitp-analytics-data/data-analyses/ntd/"
# ntd_metrics_merge.to_parquet(f"{gcs_path}puc_analysis_data_2025_12_9.parquet")

### read in cleaned ata

In [6]:
ntd_metrics_merge = pd.read_parquet(f"{gcs_path}puc_analysis_data.parquet") #puc_analysis_data.parquet is initial analysis data
ntd_metrics_merge.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4152 entries, 0 to 4151
Data columns (total 17 columns):
 #   Column             Non-Null Count  Dtype   
---  ------             --------------  -----   
 0   ntd_id             4002 non-null   object  
 1   source_agency      4152 non-null   object  
 2   agency_status      4152 non-null   object  
 3   primary_uza_name   4152 non-null   object  
 4   uza_population     4152 non-null   int64   
 5   uza_area_sq_miles  4152 non-null   float64 
 6   year               4152 non-null   int64   
 7   mode               4152 non-null   object  
 8   service            4152 non-null   object  
 9   reporter_type      4152 non-null   object  
 10  total_vrh          2623 non-null   float64 
 11  total_upt          2623 non-null   float64 
 12  total_pmt          2623 non-null   float64 
 13  ntd_id_2022        3798 non-null   object  
 14  county             3798 non-null   object  
 15  caltrans_district  3798 non-null   object  
 16  _merge

**everything matches, moving with `ntd_metrics_merge` since its has mode/service**

In [21]:
### save cleaned data to csv
ntd_metrics_merge.to_csv(f"{gcs_path}puc_analysis_data_2025_12_9.csv")

## Group aggregations

In [32]:
# melt big DF so all columns are under 1 column.
group_list_melt = [
    "source_agency",
    "year",
    "ntd_id",
    "reporter_type",
    "caltrans_district",
    "mode",
    "type_of_service"
]

value_cols = ["total_upt", "total_vrh", "total_pmt"]

melt = pd.melt(
    ntd_metrics_merge,
    id_vars=group_list_melt,
    value_vars=value_cols,
    var_name="metric",
    value_name="metric_value",
    ignore_index=True,
)

In [33]:
melt.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 9756 entries, 0 to 9755
Data columns (total 9 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   source_agency      9756 non-null   object 
 1   year               9756 non-null   int64  
 2   ntd_id             9756 non-null   object 
 3   reporter_type      9756 non-null   object 
 4   caltrans_district  9756 non-null   object 
 5   mode               9756 non-null   object 
 6   type_of_service    9756 non-null   object 
 7   metric             9756 non-null   object 
 8   metric_value       6324 non-null   float64
dtypes: float64(1), int64(1), object(7)
memory usage: 686.1+ KB


In [34]:
melt.sort_values(by=['ntd_id',"year"])

source_agency  \
1                                                          San Francisco Bay Area Rapid Transit District (BART)   
10                                                         San Francisco Bay Area Rapid Transit District (BART)   
16                                                         San Francisco Bay Area Rapid Transit District (BART)   
17                                                         San Francisco Bay Area Rapid Transit District (BART)   
19                                                         San Francisco Bay Area Rapid Transit District (BART)   
3253                                                       San Francisco Bay Area Rapid Transit District (BART)   
3262                                                       San Francisco Bay Area Rapid Transit District (BART)   
3268                                                       San Francisco Bay Area Rapid Transit District (BART)   
3269                                                       San Francisco Bay Area Rapid Transit District (BART)   
3271                                                       San Francisco Bay Area Rapid Transit District (BART)   
6505                                                       San Francisco Bay Area Rapid Transit District (BART)   
6514                                                       San Francisco Bay Area Rapid Transit District (BART)   
6520                                                       San Francisco Bay Area Rapid Transit District (BART)   
6521                                                       San Francisco Bay Area Rapid Transit District (BART)   
6523                                                       San Francisco Bay Area Rapid Transit District (BART)   
11                                                         San Francisco Bay Area Rapid Transit District (BART)   
12                                                         San Francisco Bay Area Rapid Transit District (BART)   
13                                                         San Francisco Bay Area Rapid Transit District (BART)   
14                                                         San Francisco Bay Area Rapid Transit District (BART)   
18                                                         San Francisco Bay Area Rapid Transit District (BART)   
3263                                                       San Francisco Bay Area Rapid Transit District (BART)   
3264                                                       San Francisco Bay Area Rapid Transit District (BART)   
3265                                                       San Francisco Bay Area Rapid Transit District (BART)   
3266                                                       San Francisco Bay Area Rapid Transit District (BART)   
3270                                                       San Francisco Bay Area Rapid Transit District (BART)   
6515                                                       San Francisco Bay Area Rapid Transit District (BART)   
6516                                                       San Francisco Bay Area Rapid Transit District (BART)   
6517                                                       San Francisco Bay Area Rapid Transit District (BART)   
6518                                                       San Francisco Bay Area Rapid Transit District (BART)   
6522                                                       San Francisco Bay Area Rapid Transit District (BART)   
0                                                          San Francisco Bay Area Rapid Transit District (BART)   
2                                                          San Francisco Bay Area Rapid Transit District (BART)   
4                                                          San Francisco Bay Area Rapid Transit District (BART)   
5                                                          San Francisco Bay Area Rapid Transit District (BART)   
9                                                          San Francisco 

In [35]:
### save melted data to csv
melt.to_csv(f"{gcs_path}puc_analysis_data_melt_2025_12_9.csv")

In [38]:
# What does group/agg the melted DF look like?
group_list_agg = [
    "source_agency",
    "year",
    "ntd_id",
    "reporter_type",
    "caltrans_district",
]
vrh_total = (
    melt[melt["metric"] == "total_vrh"]
    .groupby(group_list_agg)["metric_value"]
    .sum()
    .reset_index()
).rename(columns={"metric_value": "total_vrh"})

upt_total = (
    melt[melt["metric"] == "total_upt"]
    .groupby(group_list_agg)["metric_value"]
    .sum()
    .reset_index()
).rename(columns={"metric_value": "total_upt"})

passenger_total = (
    melt[melt["metric"] == "total_pmt"]
    .groupby(group_list_agg)["metric_value"]
    .sum()
    .reset_index()
).rename(columns={"metric_value": "total_pmt"})

yearly_totals = (
    ntd_metrics_merge.groupby(["year"])
    .agg({"total_upt": "sum", "total_vrh": "sum", "total_pmt": "sum"})
    .reset_index()
) 

agency_totals = (
    ntd_metrics_merge.groupby(["year","source_agency"])
    .agg({"total_upt": "sum", "total_vrh": "sum", "total_pmt": "sum"})
    .reset_index()
)

district_totals = (
    ntd_metrics_merge.groupby(["caltrans_district","year"])
    .agg({"total_upt": "sum", "total_vrh": "sum", "total_pmt": "sum"})
    .reset_index()
)

mode_totals = (
    ntd_metrics_merge.groupby(["mode","year"])
    .agg({"total_upt": "sum", "total_vrh": "sum", "total_pmt": "sum"})
    .reset_index()
)

In [39]:
vrh_total

source_agency  \
0                                                                                          Access Services (AS)   
1                                                                                          Access Services (AS)   
2                                                                                          Access Services (AS)   
3                                                                                          Access Services (AS)   
4                                                                                          Access Services (AS)   
5                                                                                          Access Services (AS)   
6                                                                         Alameda-Contra Costa Transit District   
7                                                                         Alameda-Contra Costa Transit District   
8                                                                         Alameda-Contra Costa Transit District   
9                                                                         Alameda-Contra Costa Transit District   
10                                                                        Alameda-Contra Costa Transit District   
11                                                                        Alameda-Contra Costa Transit District   
12                                                                              Altamont Corridor Express (ACE)   
13                                                                              Altamont Corridor Express (ACE)   
14                                                                              Altamont Corridor Express (ACE)   
15                                                                              Altamont Corridor Express (ACE)   
16                                                                              Altamont Corridor Express (ACE)   
17                                                                              Altamont Corridor Express (ACE)   
18                                                                                          Amador Transit (AT)   
19                                                                                          Amador Transit (AT)   
20                                                                                          Amador Transit (AT)   
21                                                                                          Amador Transit (AT)   
22                                                                                          Amador Transit (AT)   
23                                                                                          Amador Transit (AT)   
24                                                                         Anaheim Transportation Network (ATN)   
25                                                                         Anaheim Transportation Network (ATN)   
26                                                                         Anaheim Transportation Network (ATN)   
27                                                                         Anaheim Transportation Network (ATN)   
28                                                                         Anaheim Transportation Network (ATN)   
29                                                                         Anaheim Transportation Network (ATN)   
30                                                                     Antelope Valley Transit Authority (AVTA)   
31                                                                     Antelope Valley Transit Authority (AVTA)   
32                                                                     Antelope Valley Transit Authority (AVTA)   
33                                                                     Antelope Valley Transit Authority (AVTA)   
34                                                                     An

In [ ]:
# how many rows have zero PMT?
len(passenger_total[passenger_total["total_pmt"] == 0])

### chart functtion with mean line

In [ ]:
def make_chart(data, x_col, y_col, title, color_col = False):
    chart = (alt.Chart(data)
        .mark_line(point=True)
        .encode(
            x=x_col,
            y=alt.Y(f"{y_col}:Q", title=f"{y_col}", axis=alt.Axis(format=",.1f")),
            tooltip=[alt.Tooltip(f"{y_col}",format=",.1f")],
            color = color_col if color_col else alt.Undefined
        )
        .properties(
            title= title,
            height=600,
            width=800,
        )
        .interactive()
    )

    # line for average
    line = (
        alt.Chart(data)
        .mark_rule(color="red", strokeWidth=1, strokeDash=[10, 5], point=True)
        .encode(
            y=alt.Y(f"mean({y_col}):Q"),
            tooltip=[alt.Tooltip(f"mean({y_col}):Q",format=",.1f")],
        )
    )

    return display(chart + line)

## Overall Totals

### Metric grand total per year

In [ ]:
for col in yearly_totals.columns[1:]:
    yearly_avg = format(yearly_totals[col].mean(),",.2f")
    
    print(f"\nAverage {col} per  by year: {yearly_avg}"),
    make_chart(
        data = yearly_totals, 
        y_col = col,
        x_col = "year:N",
        title = f"Grand Total {col} per year",
    )


#### Boxplot of each metric grand total per year

In [ ]:
all_totals_dict = {
    "total_vrh": vrh_total,
    "total_upt": upt_total,
    "total_pmt": passenger_total,
}

# Boxplot
# removing zero-values to see what happens
for col, df in all_totals_dict.items():
    box_plot = (
        alt.Chart(df[df[col] != 0])
        .mark_boxplot(extent="min-max")
        .encode(
            x="year:N",
            y=alt.Y(col, axis=alt.Axis(format=",.1f")),
            # row = "reporter_type",
            tooltip=["source_agency", alt.Tooltip(col, format=",.1f"), "year"],
        )
        .interactive()
        .properties(title=col, height=200, width=1000)
    )

    display(
        f"Number of Agencies that reported zero {col}: {df[df[col]==0].ntd_id.nunique()}",
        box_plot.resolve_scale(y="independent"),
    )

### Metrics grand total by district, per year

In [ ]:
for col in district_totals.columns[2:]:
    district_avg = format(district_totals[col].mean(),",.2f")
    
    print(f"\nAverage {col} per  by year: {district_avg}"),
    make_chart(
        data = district_totals,
        y_col = col,
        x_col = "year:N",
        color_col = "caltrans_district",
        title = f"{col} by district per year"
    )

#### Box Plot of metric per district

In [ ]:
# Boxplot
# removing zero-values to see what happens
for col in district_totals.columns[2:]:
    box_plot = (
        alt.Chart(district_totals[district_totals[col] != 0])
        .mark_boxplot(extent="min-max")
        .encode(
            x="caltrans_district:N",
            y=col,
            # row = "reporter_type",
            tooltip=[col, "year"],
        )
        .interactive()
        .properties(title=f"Box Plot of {col} per district", height=200, width=1000)
    )

    display(
        f"\nNumber of rows that reported zero {col}: {district_totals[district_totals[col]==0][col].count()}",
        box_plot.resolve_scale(y="independent"),
    )

### Metrics grand total by agency, per year

In [ ]:
agency_avg = format(agency_totals[col].mean(),",.2f")

for col in agency_totals.columns[2:]:
    agency_avg = format(agency_totals[col].mean(),",.2f")
    
    print(f"\nAverage {col} per agency by year: {agency_avg}"),
    make_chart(
        data = agency_totals,
        y_col = col,
        x_col = "year:N",
        color_col = "source_agency:N",
        title = f"{col} per agency by year"
    )

### Metrics grand total by mode, per year

In [ ]:
for col in mode_totals.columns[2:]:
    mode_avg = format(mode_totals[col].mean(),",.2f")
    
    print(f"\nAverage {col} per mode by year: {mode_avg}"),
    make_chart(
        data = mode_totals,
        y_col = col,
        x_col = 'year:N',
        color_col = "mode:N",
        title = f"{col} per Mode by year",
    )
    